In [59]:
import pandas as pd
from Bio import SeqIO
from Bio.SeqRecord import SeqRecord
import pickle

In [60]:
DEBUG = False

# OrthoGroups to MSA 
+ load table with the proteins - orthogrous distribution 
+ filter the core orthogroups 
+ load proteins .pkl database
+ get the proteins and the genome positions corresponding to the core OGs

ids = 'korea2' #'rso_test'  #

core_ogs = '/Users/devseeva/Desktop/work/rso/OrthoFinder/orthoF_msa_'+ids+'/Species_Tree/Orthogroups_for_concatenated_alignment.txt'
ogs2prot = '/Users/devseeva/Desktop/work/rso/OrthoFinder/orthoF_msa_'+ids+'/Orthogroups/Orthogroups.tsv'
prot_db = pd.read_pickle('../'+ids+'_outputs/GENOME_PROTEIN_DB_'+ids+'.pkl')
path_p_aln = '/Users/devseeva/Desktop/work/rso/OrthoFinder/orthoF_msa_'+ids+'/MultipleSequenceAlignments/'

msa_out_fasta = '/Users/devseeva/Desktop/work/sm_workflow/snakefiles/'+ids+'_concat.fasta'
msa_out_phylip = '/Users/devseeva/Desktop/work/sm_workflow/snakefiles/'+ids+'_concat.nexus'
msa_out_xmfa_path = '/Users/devseeva/Desktop/work/sm_workflow/snakefiles/'+ids+'_concat.xmfa'
aln2acc = '/Users/devseeva/Desktop/work/sm_workflow/snakefiles/outputs/MSA_ACC_DB_'+ids+'.pkl'

In [ ]:
core_ogs = snakemake.input["core_ogs"]
ogs2prot = snakemake.input["ogs2prot"]
prot_db = pd.read_pickle(snakemake.input["prot_db"])
path_p_aln = snakemake.input["path2aln"]

msa_out_fasta = snakemake.output["msa_fasta"]
msa_out_phylip = snakemake.output["msa_phylip"]
msa_out_xmfa_path = snakemake.output["msa_xmfa"]
aln2acc = snakemake.output["aln2acc"]

In [62]:
strainsNames2fileNames = {}
for c in prot_db.columns:
    strainsNames2fileNames[c.split('$')[1]] = c.split('$')[0]
strainsNames2fileNames

{'to53': 'to53',
 'pe1': 'Pe_1',
 'pe15': 'pe15',
 'pe3': 'Pe_3',
 'pe13': 'pe13',
 'pe39': 'Pe_39',
 'pe61': 'pe61',
 'to7': 'to7',
 'to36': 'to36',
 'to1': 'to1',
 'pe56': 'pe56',
 'pe57': 'Pe_57',
 'to28': 'to28',
 'pe9': 'pe9',
 'pe27': 'Pe_27',
 'pe26': 'pe26',
 'to63': 'to63',
 'pe18': 'pe18_round_3.fasta',
 'pe30': 'pe30'}

In [63]:
prot_db = prot_db.rename(columns=lambda x: str(x).split('$')[0])
prot_db

to53 Pe_1 pe15  \
GDEOEPAP_00001  {'chr': '1', 'location': (30, 31, 32, 33, 34, ...  NaN  NaN   
GDEOEPAP_00002  {'chr': '1', 'location': (1876, 1877, 1878, 18...  NaN  NaN   
GDEOEPAP_00003  {'chr': '1', 'location': (3128, 3129, 3130, 31...  NaN  NaN   
GDEOEPAP_00004  {'chr': '1', 'location': (7139, 7138, 7137, 71...  NaN  NaN   
GDEOEPAP_00005  {'chr': '1', 'location': (8581, 8582, 8583, 85...  NaN  NaN   
...                                                           ...  ...  ...   
EENJCLCO_05336                                                NaN  NaN  NaN   
EENJCLCO_05337                                                NaN  NaN  NaN   
EENJCLCO_05338                                                NaN  NaN  NaN   
EENJCLCO_05339                                                NaN  NaN  NaN   
EENJCLCO_05340                                                NaN  NaN  NaN   

               Pe_3 pe13 Pe_39 pe61  to7 to36  to1 pe56 Pe_57 to28  pe9 Pe_27  \
GDEOEPAP_00001  NaN  NaN   NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN  NaN   NaN   
GDEOEPAP_00002  NaN  NaN   NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN  NaN   NaN   
GDEOEPAP_00003  NaN  NaN   NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN  NaN   NaN   
GDEOEPAP_00004  NaN  NaN   NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN  NaN   NaN   
GDEOEPAP_00005  NaN  NaN   NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN  NaN   NaN   
...             ...  ...   ...  ...  ...  ...  ...  ...   ...  ...  ...   ...   
EENJCLCO_05336  NaN  NaN   NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN  NaN   NaN   
EENJCLCO_05337  NaN  NaN   NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN  NaN   NaN   
EENJCLCO_05338  NaN  NaN   NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN  NaN   NaN   
EENJCLCO_05339  NaN  NaN   NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN  NaN   NaN   
EENJCLCO_05340  NaN  NaN   NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN  NaN   NaN   

               pe26 to63 pe18_round_3.fasta  \
GDEOEPAP_00001  NaN  NaN                NaN   
GDEOEPAP_00002  NaN  NaN                NaN   
GDEOEPAP_00003  NaN  NaN                NaN   
GDEOEPAP_00004  NaN  NaN                NaN   
GDEOEPAP_00005  NaN  NaN                NaN   
...             ...  ...                ...   
EENJCLCO_05336  NaN  NaN                NaN   
EENJCLCO_05337  NaN  NaN                NaN   
EENJCLCO_05338  NaN  NaN                NaN   
EENJCLCO_05339  NaN  NaN                NaN   
EENJCLCO_05340  NaN  NaN                NaN   

                                                             pe30  
GDEOEPAP_00001                                                NaN  
GDEOEPAP_00002                                                NaN  
GDEOEPAP_00003                                                NaN  
GDEOEPAP_00004                                                NaN  
GDEOEPAP_00005                                                NaN  
...                                                           ...  
EENJCLCO_05336  {'chr': 'cluster_012', 'location': (8609, 8610...  
EENJCLCO_05337  {'chr': 'cluster_012', 'location': (10200, 101...  
EENJCLCO_05338  {'chr': 'cluster_012', 'location': (11858, 118...  
EENJCLCO_05339  {'chr': 'cluster_012', 'location': (12330, 123...  
EENJCLCO_05340  {'chr': 'cluster_012', 'location': (12668, 126...  

[84011 rows x 19 columns]

In [64]:
# get core ogs
f = open(core_ogs,"r")
ogs = []
for l in f:
    ogs.append(l.replace('\n',''))
f.close()
##print(ogs)

In [65]:
# load roteins ids from the OGs table 
# keep only the core OGs

tab_prot = pd.read_csv(ogs2prot, sep='\t', index_col=0)  
tab_prot = tab_prot.loc[ogs]
tab_prot = tab_prot.rename(columns=lambda x: str(x).replace('_protein','')) # ncbi file names correction
tab_prot = tab_prot.rename(columns=strainsNames2fileNames)
tab_prot

Pe_1            pe13            pe15 pe18_round_3.fasta  \
Orthogroup                                                                      
OG0000211   WP_003261842.1  AIELFPIA_03026  BODOBMNI_02989     NICADNEC_00844   
OG0000212   WP_003261911.1  AIELFPIA_01437  BODOBMNI_01473     NICADNEC_02976   
OG0000213   WP_003261929.1  AIELFPIA_01452  BODOBMNI_01488     NICADNEC_02991   
OG0000214   WP_003261939.1  AIELFPIA_01459  BODOBMNI_01495     NICADNEC_02998   
OG0000215   WP_003261941.1  AIELFPIA_01461  BODOBMNI_01497     NICADNEC_03000   
...                    ...             ...             ...                ...   
OG0004004   WP_225891747.1  AIELFPIA_04069  BODOBMNI_04036     NICADNEC_03941   
OG0004005   WP_225891750.1  AIELFPIA_03907  BODOBMNI_03873     NICADNEC_03778   
OG0004006   WP_225891752.1  AIELFPIA_03879  BODOBMNI_03845     NICADNEC_03750   
OG0004007   WP_225891753.1  AIELFPIA_03858  BODOBMNI_03824     NICADNEC_03729   
OG0004008   WP_225891755.1  AIELFPIA_03823  BODOBMNI_03789     NICADNEC_03693   

                      pe26           Pe_27            Pe_3            pe30  \
Orthogroup                                                                   
OG0000211   NCAEKIBJ_02782  WP_003261842.1  WP_003261842.1  EENJCLCO_02906   
OG0000212   NCAEKIBJ_01412  WP_003261911.1  WP_003261911.1  EENJCLCO_01433   
OG0000213   NCAEKIBJ_01427  WP_003261929.1  WP_003261929.1  EENJCLCO_01448   
OG0000214   NCAEKIBJ_01434  WP_003261939.1  WP_003261939.1  EENJCLCO_01455   
OG0000215   NCAEKIBJ_01436  WP_003261941.1  WP_003261941.1  EENJCLCO_01457   
...                    ...             ...             ...             ...   
OG0004004   NCAEKIBJ_04729  WP_081365349.1  WP_052331360.1  EENJCLCO_03981   
OG0004005   NCAEKIBJ_04891  WP_071507083.1  WP_064047918.1  EENJCLCO_03818   
OG0004006   NCAEKIBJ_04921  WP_038937612.1  WP_038937612.1  EENJCLCO_03790   
OG0004007   NCAEKIBJ_04943  WP_071624131.1  WP_118888109.1  EENJCLCO_03769   
OG0004008   NCAEKIBJ_04975  WP_081365355.1  WP_019719048.1  EENJCLCO_03734   

                     Pe_39            pe56           Pe_57            pe61  \
Orthogroup                                                                   
OG0000211   WP_003261842.1  HFPKLCHG_02865  WP_003261842.1  KPJNPNMP_02960   
OG0000212   WP_003261911.1  HFPKLCHG_01383  WP_003261911.1  KPJNPNMP_01417   
OG0000213   WP_003261929.1  HFPKLCHG_01398  WP_003261929.1  KPJNPNMP_01432   
OG0000214   WP_003261939.1  HFPKLCHG_01405  WP_003261939.1  KPJNPNMP_01439   
OG0000215   WP_003261941.1  HFPKLCHG_01407  WP_003261941.1  KPJNPNMP_01441   
...                    ...             ...             ...             ...   
OG0004004   WP_165858710.1  HFPKLCHG_03918  WP_167798393.1  KPJNPNMP_04008   
OG0004005   WP_071507083.1  HFPKLCHG_03753  WP_071507083.1  KPJNPNMP_03846   
OG0004006   WP_089190982.1  HFPKLCHG_03721  WP_071507970.1  KPJNPNMP_03814   
OG0004007   WP_165858715.1  HFPKLCHG_03696  WP_071507860.1  KPJNPNMP_03789   
OG0004008   WP_089190975.1  HFPKLCHG_03659  WP_081365371.1  KPJNPNMP_03752   

                       pe9             to1            to28            to36  \
Orthogroup                                                                   
OG0000211   BANHGPCM_02826  JICADCBL_03005  IIHHNEFC_00800  FAFFGKOF_02936   
OG0000212   BANHGPCM_01414  JICADCBL_01454  IIHHNEFC_02313  FAFFGKOF_01401   
OG0000213   BANHGPCM_01429  JICADCBL_01469  IIHHNEFC_02298  FAFFGKOF_01416   
OG0000214   BANHGPCM_01436  JICADCBL_01476  IIHHNEFC_02291  FAFFGKOF_01423   
OG0000215   BANHGPCM_01438  JICADCBL_01478  IIHHNEFC_02289  FAFFGKOF_01425   
...                    ...             ...             ...             ...   
OG0004004   BANHGPCM_03905  JICADCBL_04053  IIHHNEFC_03963  FAFFGKOF_04015   
OG0004005   BANHGPCM_03744  JICADCBL_03889  IIHHNEFC_03802  FAFFGKOF_03854   
OG0004006   BANHGPCM_03715  JICADCBL_03859  IIHHNEFC_03773  FAFFGKOF_03825   
OG0004007   BANHGPCM_03694  JICADCBL_03836  IIHHNEFC_03752  FAFFGKOF_03804   
OG

In [66]:
genomes_for_og = list(tab_prot.columns) 
genomes_for_og

['Pe_1',
 'pe13',
 'pe15',
 'pe18_round_3.fasta',
 'pe26',
 'Pe_27',
 'Pe_3',
 'pe30',
 'Pe_39',
 'pe56',
 'Pe_57',
 'pe61',
 'pe9',
 'to1',
 'to28',
 'to36',
 'to53',
 'to63',
 'to7']

# Get Nucleotide sequences + corresponding positions in genome

# Load single proteins alignments and extract gaps

In [67]:
tab_prot

Pe_1            pe13            pe15 pe18_round_3.fasta  \
Orthogroup                                                                      
OG0000211   WP_003261842.1  AIELFPIA_03026  BODOBMNI_02989     NICADNEC_00844   
OG0000212   WP_003261911.1  AIELFPIA_01437  BODOBMNI_01473     NICADNEC_02976   
OG0000213   WP_003261929.1  AIELFPIA_01452  BODOBMNI_01488     NICADNEC_02991   
OG0000214   WP_003261939.1  AIELFPIA_01459  BODOBMNI_01495     NICADNEC_02998   
OG0000215   WP_003261941.1  AIELFPIA_01461  BODOBMNI_01497     NICADNEC_03000   
...                    ...             ...             ...                ...   
OG0004004   WP_225891747.1  AIELFPIA_04069  BODOBMNI_04036     NICADNEC_03941   
OG0004005   WP_225891750.1  AIELFPIA_03907  BODOBMNI_03873     NICADNEC_03778   
OG0004006   WP_225891752.1  AIELFPIA_03879  BODOBMNI_03845     NICADNEC_03750   
OG0004007   WP_225891753.1  AIELFPIA_03858  BODOBMNI_03824     NICADNEC_03729   
OG0004008   WP_225891755.1  AIELFPIA_03823  BODOBMNI_03789     NICADNEC_03693   

                      pe26           Pe_27            Pe_3            pe30  \
Orthogroup                                                                   
OG0000211   NCAEKIBJ_02782  WP_003261842.1  WP_003261842.1  EENJCLCO_02906   
OG0000212   NCAEKIBJ_01412  WP_003261911.1  WP_003261911.1  EENJCLCO_01433   
OG0000213   NCAEKIBJ_01427  WP_003261929.1  WP_003261929.1  EENJCLCO_01448   
OG0000214   NCAEKIBJ_01434  WP_003261939.1  WP_003261939.1  EENJCLCO_01455   
OG0000215   NCAEKIBJ_01436  WP_003261941.1  WP_003261941.1  EENJCLCO_01457   
...                    ...             ...             ...             ...   
OG0004004   NCAEKIBJ_04729  WP_081365349.1  WP_052331360.1  EENJCLCO_03981   
OG0004005   NCAEKIBJ_04891  WP_071507083.1  WP_064047918.1  EENJCLCO_03818   
OG0004006   NCAEKIBJ_04921  WP_038937612.1  WP_038937612.1  EENJCLCO_03790   
OG0004007   NCAEKIBJ_04943  WP_071624131.1  WP_118888109.1  EENJCLCO_03769   
OG0004008   NCAEKIBJ_04975  WP_081365355.1  WP_019719048.1  EENJCLCO_03734   

                     Pe_39            pe56           Pe_57            pe61  \
Orthogroup                                                                   
OG0000211   WP_003261842.1  HFPKLCHG_02865  WP_003261842.1  KPJNPNMP_02960   
OG0000212   WP_003261911.1  HFPKLCHG_01383  WP_003261911.1  KPJNPNMP_01417   
OG0000213   WP_003261929.1  HFPKLCHG_01398  WP_003261929.1  KPJNPNMP_01432   
OG0000214   WP_003261939.1  HFPKLCHG_01405  WP_003261939.1  KPJNPNMP_01439   
OG0000215   WP_003261941.1  HFPKLCHG_01407  WP_003261941.1  KPJNPNMP_01441   
...                    ...             ...             ...             ...   
OG0004004   WP_165858710.1  HFPKLCHG_03918  WP_167798393.1  KPJNPNMP_04008   
OG0004005   WP_071507083.1  HFPKLCHG_03753  WP_071507083.1  KPJNPNMP_03846   
OG0004006   WP_089190982.1  HFPKLCHG_03721  WP_071507970.1  KPJNPNMP_03814   
OG0004007   WP_165858715.1  HFPKLCHG_03696  WP_071507860.1  KPJNPNMP_03789   
OG0004008   WP_089190975.1  HFPKLCHG_03659  WP_081365371.1  KPJNPNMP_03752   

                       pe9             to1            to28            to36  \
Orthogroup                                                                   
OG0000211   BANHGPCM_02826  JICADCBL_03005  IIHHNEFC_00800  FAFFGKOF_02936   
OG0000212   BANHGPCM_01414  JICADCBL_01454  IIHHNEFC_02313  FAFFGKOF_01401   
OG0000213   BANHGPCM_01429  JICADCBL_01469  IIHHNEFC_02298  FAFFGKOF_01416   
OG0000214   BANHGPCM_01436  JICADCBL_01476  IIHHNEFC_02291  FAFFGKOF_01423   
OG0000215   BANHGPCM_01438  JICADCBL_01478  IIHHNEFC_02289  FAFFGKOF_01425   
...                    ...             ...             ...             ...   
OG0004004   BANHGPCM_03905  JICADCBL_04053  IIHHNEFC_03963  FAFFGKOF_04015   
OG0004005   BANHGPCM_03744  JICADCBL_03889  IIHHNEFC_03802  FAFFGKOF_03854   
OG0004006   BANHGPCM_03715  JICADCBL_03859  IIHHNEFC_03773  FAFFGKOF_03825   
OG0004007   BANHGPCM_03694  JICADCBL_03836  IIHHNEFC_03752  FAFFGKOF_03804   
OG

In [68]:
gaps2tab = pd.DataFrame(columns=tab_prot.columns, index=tab_prot.index)

for og in ogs:
    pmsa = path_p_aln + '/' +og + '.fa'
    for record in SeqIO.parse(pmsa, "fasta"):  
        #print(record.id)
        
        # prokka/ncbi genomes header structure 
        header = record.id.split('_')
        protein_id = header[-2]+'_'+header[-1]
        genome_id = strainsNames2fileNames[record.id.replace(protein_id, '').replace('protein_', '')[:-1].replace('_1_', '.1_')]
        
        #print(pmsa)
        #print(protein_id, genome_id)
        
        # EXACT GAPS MAPPING 
        gaps_bool = []
        for aa in record.seq:
            if aa == '-':
                gaps_bool.append(1) 
                gaps_bool.append(1) 
                gaps_bool.append(1) 
            else:
                gaps_bool.append(0) 
                gaps_bool.append(0) 
                gaps_bool.append(0)
        
        prot_db.loc[protein_id, genome_id]['aln_gaps'] = gaps_bool
        gaps2tab.loc[og][genome_id] = gaps_bool
gaps2tab

Pe_1  \
Orthogroup                                                      
OG0000211   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000212   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000213   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000214   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000215   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
...                                                       ...   
OG0004004   [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
OG0004005   [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
OG0004006   [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
OG0004007   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0004008   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                                         pe13  \
Orthogroup                                                      
OG0000211   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000212   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000213   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000214   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000215   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
...                                                       ...   
OG0004004   [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
OG0004005   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0004006   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0004007   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0004008   [1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                                         pe15  \
Orthogroup                                                      
OG0000211   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000212   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000213   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000214   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000215   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
...                                                       ...   
OG0004004   [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
OG0004005   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0004006   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0004007   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0004008   [1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                           pe18_round_3.fasta  \
Orthogroup                                                      
OG0000211   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000212   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000213   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000214   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000215   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
...                                                       ...   
OG0004004   [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
OG0004005   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0004006   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0004007   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0004008   [1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                                         pe26  \
Orthogroup                                                      
OG0000211   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000212   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000213   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000214   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0000215   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
...                                                       ...   
OG0004004   [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...   
OG0004005   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
OG0004006   [0, 0, 0, 0

# Genome-based solution
+ for each genome grab the cols of the core OG table
+ concatenate the corresponding nucleotides from the GENOME_PROTEIN_DB

## TODO length of nucleotides is larger than length of translation*3 ?!

In [70]:
g2nucl = {}
g2pos = {}
g2chr = {}
g2strand = {}
g2acc = {}
g2gaps = {}

#nucl_fasta = open("core_OG_nucl.fasta", "w") # DEBUG write out

for g in genomes_for_og:
    print('Genome', g)
    
    # get corresponding nucleotide positions 
    g2pos[g] = []
    # get corresponding chr ids 
    g2chr[g] = []
    # get corresponding strands
    g2strand[g] = []
    # get protein accession for each genome position
    ####g2acc[g.split('.1_')[1][:10]] = []
    g2acc[g] = []
    
    g2gaps[g] = []
    
    # get nucleotide sequences for all the core og proteins per genome 
    nucl_per_genome = []
    
    for i in prot_db.loc[tab_prot[g].values, g]: 
        nucl_per_genome.append(str(i['nucl']))
        g2pos[g].extend(i['location'])
        #g2chr[g].append((i['chr'], len(i['nucl'])))
        prot_len = len(i['nucl']) ######################## <-----
        for counter in range(len(i['aln_gaps'])):
            if DEBUG:
                g2chr[g].append(i['chr'])
                g2strand[g].append(i['location'].strand)
            #g2acc[g.split('.1_')[1][:10]].append(i['acc']) # phylip name format
            g2acc[g].append(i['acc']) # phylip name format
        g2gaps[g].extend(i['aln_gaps'])
    
    nucl_per_genome = "".join(nucl_per_genome)
    g2nucl[g] = nucl_per_genome
    print('Exported sequence length', len(nucl_per_genome))
    #print('Exported protein accessions', len(g2acc[g.split('.1_')[1][:10]]))
    print('Exported alignment gaps', len(g2gaps[g]))
    print('Exported original positions', len(g2pos[g]))
    print('Exported chr labels', len(g2chr[g]))
    print('Exported strands', len(g2strand[g]))
    #nucl_fasta.write('>'+g+'\n')
    #nucl_fasta.write(nucl_per_genome+'\n')
    print()
    
#nucl_fasta.close()

Genome Pe_1
Exported sequence length 3816086
Exported alignment gaps 3833073
Exported original positions 3816086
Exported chr labels 0
Exported strands 0

Genome pe13
Exported sequence length 3821283
Exported alignment gaps 3833073
Exported original positions 3821283
Exported chr labels 0
Exported strands 0

Genome pe15
Exported sequence length 3822027
Exported alignment gaps 3833073
Exported original positions 3822027
Exported chr labels 0
Exported strands 0

Genome pe18_round_3.fasta
Exported sequence length 3819984
Exported alignment gaps 3833073
Exported original positions 3819984
Exported chr labels 0
Exported strands 0

Genome pe26
Exported sequence length 3821691
Exported alignment gaps 3833073
Exported original positions 3821691
Exported chr labels 0
Exported strands 0

Genome Pe_27
Exported sequence length 3814092
Exported alignment gaps 3833073
Exported original positions 3814092
Exported chr labels 0
Exported strands 0

Genome Pe_3
Exported sequence length 3812706
Exported a

In [71]:
# SAVE PROTEIN ACC FOR MAPPING

with open(aln2acc, 'wb') as handle:
    pickle.dump(g2acc, handle, protocol=pickle.HIGHEST_PROTOCOL)

# replace ambiguous bases with gaps!

In [72]:
for g in g2nucl:
    atcg = {'A', 'C', 'T', 'G'}
    ambig = set(g2nucl[g]).difference(atcg)
    
    print("before", set(g2nucl[g]))
    for b in ambig:
        g2nucl[g] = g2nucl[g].replace(b, '-')
    print("after ",set(g2nucl[g]))

before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A', 'T'}
before {'C', 'G', 'A', 'T'}
after  {'C', 'G', 'A

In [73]:
#str(prot_db.loc["WP_097388881.1","GCF_002501565.1_ASM250156v1_protein"]['nucl'])
#for v in prot_db['GCF_001587135.1_ASM158713v1_protein'].values:
#    print(v)

# Export MSA

In [74]:
msa_fasta = open(msa_out_fasta, "w")
for g in g2nucl:
    print(g, len(g2nucl[g]))
    msa_fasta.write('>'+g+'\n') ##+g.split('_')[2][:10]+'\n')
    
    i = 0
    for gap in g2gaps[g]:
        if gap:
            msa_fasta.write('-')
        else:
            msa_fasta.write(g2nucl[g][i])
            i = i + 1
    msa_fasta.write('\n')
msa_fasta.close()

Pe_1 3816086
pe13 3821283
pe15 3822027
pe18_round_3.fasta 3819984
pe26 3821691
Pe_27 3814092
Pe_3 3812706
pe30 3822162
Pe_39 3815841
pe56 3818712
Pe_57 3815898
pe61 3820110
pe9 3822306
to1 3820794
to28 3820920
to36 3822519
to53 3806394
to63 3817668
to7 3817827


# Convert to Phylip

In [76]:
#SeqIO.convert(msa_out_fasta, "fasta", msa_out_phylip, "nexus")

nexus = open(msa_out_phylip, 'w')
nexus.write('#NEXUS\n')
nexus.write('begin data;\n')
nexus.write('dimensions ntax='+str(len(strainsNames2fileNames))+' nchar='+str(len(g2gaps[g]))+' ;\n')
nexus.write('format datatype=dna ;\n')
nexus.write('matrix\n')

for record in SeqIO.parse(msa_out_fasta, "fasta"):
    nexus.write(record.id+'\t'+str(record.seq)+'\n')
    
nexus.write(';\n')
nexus.write('end;\n')

nexus.close()
#SeqIO.write(annotated_records, msa_out_phylip, "nexus")


# Export XMFA

In [77]:
msa_out_xmfa = open(msa_out_xmfa_path, 'w')

for og in ogs:
    pmsa = path_p_aln + '/' +og + '.fa'
    for record in SeqIO.parse(pmsa, "fasta"):
        print(record.id)
        #g_id = record.id.split('_WP')[0].replace('_1_', '.1_')
        #p_id = record.id.split('_protein_')[-1]
        # prokka changes 
        ##g_id = record.id.split('_')[0]
        ##p_id = record.id.replace(record.id.split('_')[0]+'_', '')
        
        # prokka/ncbi genomes header structure 
        header = record.id.split('_')
        p_id = header[-2]+'_'+header[-1]
        g_id = strainsNames2fileNames[record.id.replace(p_id, '').replace('protein_', '')[:-1].replace('_1_', '.1_')]       
        print(g_id, p_id)
                                           
        nns = prot_db.loc[p_id, g_id]['nucl']
        #msa_out_xmfa.write('>'+record.id.split('_')[3][:10]+'\n')
        #prokka
        msa_out_xmfa.write('>'+g_id+'\n')
        
        atcg = {'A', 'T', 'G', 'C','-'}
        ambig = set(nns).difference(atcg)
        #print(ambig)
        for b in ambig:
            nns = str(nns).replace(b, '-')
        #print('aaaaaa',  nns)
        
        gaps_v = gaps2tab.loc[og, g_id]
        i = 0
        for gap in gaps_v:
            if gap:
                msa_out_xmfa.write('-')
            else:
                msa_out_xmfa.write(nns[i])
                i = i + 1
        msa_out_xmfa.write('\n')
    msa_out_xmfa.write('=' + '\n')
msa_out_xmfa.close()

pe1_WP_003261842.1
Pe_1 WP_003261842.1
pe13_AIELFPIA_03026
pe13 AIELFPIA_03026
pe15_BODOBMNI_02989
pe15 BODOBMNI_02989
pe18_NICADNEC_00844
pe18_round_3.fasta NICADNEC_00844
pe26_NCAEKIBJ_02782
pe26 NCAEKIBJ_02782
pe27_WP_003261842.1
Pe_27 WP_003261842.1
pe3_WP_003261842.1
Pe_3 WP_003261842.1
pe30_EENJCLCO_02906
pe30 EENJCLCO_02906
pe39_WP_003261842.1
Pe_39 WP_003261842.1
pe56_HFPKLCHG_02865
pe56 HFPKLCHG_02865
pe57_WP_003261842.1
Pe_57 WP_003261842.1
pe61_KPJNPNMP_02960
pe61 KPJNPNMP_02960
pe9_BANHGPCM_02826
pe9 BANHGPCM_02826
to1_JICADCBL_03005
to1 JICADCBL_03005
to28_IIHHNEFC_00800
to28 IIHHNEFC_00800
to36_FAFFGKOF_02936
to36 FAFFGKOF_02936
to53_GDEOEPAP_02558
to53 GDEOEPAP_02558
to63_BFOHDJIN_02838
to63 BFOHDJIN_02838
to7_HOLBGOEP_02887
to7 HOLBGOEP_02887
pe1_WP_003261911.1
Pe_1 WP_003261911.1
pe13_AIELFPIA_01437
pe13 AIELFPIA_01437
pe15_BODOBMNI_01473
pe15 BODOBMNI_01473
pe18_NICADNEC_02976
pe18_round_3.fasta NICADNEC_02976
pe26_NCAEKIBJ_01412
pe26 NCAEKIBJ_01412
pe27_WP_003261911.

to7 HOLBGOEP_00543
pe1_WP_003264141.1
Pe_1 WP_003264141.1
pe13_AIELFPIA_00443
pe13 AIELFPIA_00443
pe15_BODOBMNI_00463
pe15 BODOBMNI_00463
pe18_NICADNEC_02003
pe18_round_3.fasta NICADNEC_02003
pe26_NCAEKIBJ_00457
pe26 NCAEKIBJ_00457
pe27_WP_003264141.1
Pe_27 WP_003264141.1
pe3_WP_003264141.1
Pe_3 WP_003264141.1
pe30_EENJCLCO_00465
pe30 EENJCLCO_00465
pe39_WP_003264141.1
Pe_39 WP_003264141.1
pe56_HFPKLCHG_00526
pe56 HFPKLCHG_00526
pe57_WP_003264141.1
Pe_57 WP_003264141.1
pe61_KPJNPNMP_00546
pe61 KPJNPNMP_00546
pe9_BANHGPCM_00510
pe9 BANHGPCM_00510
to1_JICADCBL_00466
to1 JICADCBL_00466
to28_IIHHNEFC_03199
to28 IIHHNEFC_03199
to36_FAFFGKOF_00438
to36 FAFFGKOF_00438
to53_GDEOEPAP_00467
to53 GDEOEPAP_00467
to63_BFOHDJIN_00465
to63 BFOHDJIN_00465
to7_HOLBGOEP_00552
to7 HOLBGOEP_00552
pe1_WP_003264280.1
Pe_1 WP_003264280.1
pe13_AIELFPIA_01657
pe13 AIELFPIA_01657
pe15_BODOBMNI_01691
pe15 BODOBMNI_01691
pe18_NICADNEC_03195
pe18_round_3.fasta NICADNEC_03195
pe26_NCAEKIBJ_01629
pe26 NCAEKIBJ_01629

to7_HOLBGOEP_01641
to7 HOLBGOEP_01641
pe1_WP_003267785.1
Pe_1 WP_003267785.1
pe13_AIELFPIA_01745
pe13 AIELFPIA_01745
pe15_BODOBMNI_01779
pe15 BODOBMNI_01779
pe18_NICADNEC_03283
pe18_round_3.fasta NICADNEC_03283
pe26_NCAEKIBJ_01717
pe26 NCAEKIBJ_01717
pe27_WP_003267785.1
Pe_27 WP_003267785.1
pe3_WP_003267785.1
Pe_3 WP_003267785.1
pe30_EENJCLCO_01740
pe30 EENJCLCO_01740
pe39_WP_003267785.1
Pe_39 WP_003267785.1
pe56_HFPKLCHG_01690
pe56 HFPKLCHG_01690
pe57_WP_003267785.1
Pe_57 WP_003267785.1
pe61_KPJNPNMP_01778
pe61 KPJNPNMP_01778
pe9_BANHGPCM_01722
pe9 BANHGPCM_01722
to1_JICADCBL_01774
to1 JICADCBL_01774
to28_IIHHNEFC_01993
to28 IIHHNEFC_01993
to36_FAFFGKOF_01709
to36 FAFFGKOF_01709
to53_GDEOEPAP_01636
to53 GDEOEPAP_01636
to63_BFOHDJIN_01675
to63 BFOHDJIN_01675
to7_HOLBGOEP_01714
to7 HOLBGOEP_01714
pe1_WP_003267806.1
Pe_1 WP_003267806.1
pe13_AIELFPIA_01811
pe13 AIELFPIA_01811
pe15_BODOBMNI_01845
pe15 BODOBMNI_01845
pe18_NICADNEC_03349
pe18_round_3.fasta NICADNEC_03349
pe26_NCAEKIBJ_01778


pe27_WP_003278556.1
Pe_27 WP_003278556.1
pe3_WP_003278556.1
Pe_3 WP_003278556.1
pe30_EENJCLCO_03331
pe30 EENJCLCO_03331
pe39_WP_003278556.1
Pe_39 WP_003278556.1
pe56_HFPKLCHG_03260
pe56 HFPKLCHG_03260
pe57_WP_003278556.1
Pe_57 WP_003278556.1
pe61_KPJNPNMP_03355
pe61 KPJNPNMP_03355
pe9_BANHGPCM_03253
pe9 BANHGPCM_03253
to1_JICADCBL_03399
to1 JICADCBL_03399
to28_IIHHNEFC_00403
to28 IIHHNEFC_00403
to36_FAFFGKOF_03363
to36 FAFFGKOF_03363
to53_GDEOEPAP_02906
to53 GDEOEPAP_02906
to63_BFOHDJIN_03234
to63 BFOHDJIN_03234
to7_HOLBGOEP_03282
to7 HOLBGOEP_03282
pe1_WP_003278969.1
Pe_1 WP_003278969.1
pe13_AIELFPIA_03112
pe13 AIELFPIA_03112
pe15_BODOBMNI_03076
pe15 BODOBMNI_03076
pe18_NICADNEC_00931
pe18_round_3.fasta NICADNEC_00931
pe26_NCAEKIBJ_02894
pe26 NCAEKIBJ_02894
pe27_WP_003278969.1
Pe_27 WP_003278969.1
pe3_WP_003278969.1
Pe_3 WP_003278969.1
pe30_EENJCLCO_02993
pe30 EENJCLCO_02993
pe39_WP_003278969.1
Pe_39 WP_003278969.1
pe56_HFPKLCHG_02950
pe56 HFPKLCHG_02950
pe57_WP_003278969.1
Pe_57 WP_0

to7_HOLBGOEP_03549
to7 HOLBGOEP_03549
pe1_WP_010999996.1
Pe_1 WP_010999996.1
pe13_AIELFPIA_03689
pe13 AIELFPIA_03689
pe15_BODOBMNI_03655
pe15 BODOBMNI_03655
pe18_NICADNEC_01509
pe18_round_3.fasta NICADNEC_01509
pe26_NCAEKIBJ_03455
pe26 NCAEKIBJ_03455
pe27_WP_010999996.1
Pe_27 WP_010999996.1
pe3_WP_016722630.1
Pe_3 WP_016722630.1
pe30_EENJCLCO_03600
pe30 EENJCLCO_03600
pe39_WP_010999996.1
Pe_39 WP_010999996.1
pe56_HFPKLCHG_03526
pe56 HFPKLCHG_03526
pe57_WP_010999996.1
Pe_57 WP_010999996.1
pe61_KPJNPNMP_03620
pe61 KPJNPNMP_03620
pe9_BANHGPCM_03524
pe9 BANHGPCM_03524
to1_JICADCBL_03667
to1 JICADCBL_03667
to28_IIHHNEFC_03583
to28 IIHHNEFC_03583
to36_FAFFGKOF_03634
to36 FAFFGKOF_03634
to53_GDEOEPAP_03214
to53 GDEOEPAP_03214
to63_BFOHDJIN_03500
to63 BFOHDJIN_03500
to7_HOLBGOEP_03548
to7 HOLBGOEP_03548
pe1_WP_011000000.1
Pe_1 WP_011000000.1
pe13_AIELFPIA_03684
pe13 AIELFPIA_03684
pe15_BODOBMNI_03649
pe15 BODOBMNI_03649
pe18_NICADNEC_01504
pe18_round_3.fasta NICADNEC_01504
pe26_NCAEKIBJ_03448


...

pe39_WP_209319333.1
Pe_39 WP_209319333.1
pe56_HFPKLCHG_03663
pe56 HFPKLCHG_03663
pe57_WP_209318896.1
Pe_57 WP_209318896.1
pe61_KPJNPNMP_03756
pe61 KPJNPNMP_03756
pe9_BANHGPCM_03663
pe9 BANHGPCM_03663
to1_JICADCBL_03805
to1 JICADCBL_03805
to28_IIHHNEFC_03721
to28 IIHHNEFC_03721
to36_FAFFGKOF_03773
to36 FAFFGKOF_03773
to53_GDEOEPAP_03338
to53 GDEOEPAP_03338
to63_BFOHDJIN_03639
to63 BFOHDJIN_03639
to7_HOLBGOEP_03685
to7 HOLBGOEP_03685
pe1_WP_220140126.1
Pe_1 WP_220140126.1
pe13_AIELFPIA_03892
pe13 AIELFPIA_03892
pe15_BODOBMNI_03858
pe15 BODOBMNI_03858
pe18_NICADNEC_03763
pe18_round_3.fasta NICADNEC_03763
pe26_NCAEKIBJ_04906
pe26 NCAEKIBJ_04906
pe27_WP_011003543.1
Pe_27 WP_011003543.1
pe3_WP_020829588.1
Pe_3 WP_020829588.1
pe30_EENJCLCO_03803
pe30 EENJCLCO_03803
pe39_WP_020829588.1
Pe_39 WP_020829588.1
pe56_HFPKLCHG_03738
pe56 HFPKLCHG_03738
pe57_WP_011003543.1
Pe_57 WP_011003543.1
pe61_KPJNPNMP_03831
pe61 KPJNPNMP_03831
pe9_BANHGPCM_03729
pe9 BANHGPCM_03729
to1_JICADCBL_03874
to1 JICADCBL

pe13_AIELFPIA_04117
pe13 AIELFPIA_04117
pe15_BODOBMNI_04084
pe15 BODOBMNI_04084
pe18_NICADNEC_03989
pe18_round_3.fasta NICADNEC_03989
pe26_NCAEKIBJ_04670
pe26 NCAEKIBJ_04670
pe27_WP_011003800.1
Pe_27 WP_011003800.1
pe3_WP_071895657.1
Pe_3 WP_071895657.1
pe30_EENJCLCO_04029
pe30 EENJCLCO_04029
pe39_WP_157699218.1
Pe_39 WP_157699218.1
pe56_HFPKLCHG_03977
pe56 HFPKLCHG_03977
pe57_WP_011003800.1
Pe_57 WP_011003800.1
pe61_KPJNPNMP_04067
pe61 KPJNPNMP_04067
pe9_BANHGPCM_03953
pe9 BANHGPCM_03953
to1_JICADCBL_04101
to1 JICADCBL_04101
to28_IIHHNEFC_04011
to28 IIHHNEFC_04011
to36_FAFFGKOF_04063
to36 FAFFGKOF_04063
to53_GDEOEPAP_03622
to53 GDEOEPAP_03622
to63_BFOHDJIN_03948
to63 BFOHDJIN_03948
to7_HOLBGOEP_03996
to7 HOLBGOEP_03996
pe1_WP_223259724.1
Pe_1 WP_223259724.1
pe13_AIELFPIA_05299
pe13 AIELFPIA_05299
pe15_BODOBMNI_05268
pe15 BODOBMNI_05268
pe18_NICADNEC_05174
pe18_round_3.fasta NICADNEC_05174
pe26_NCAEKIBJ_05101
pe26 NCAEKIBJ_05101
pe27_WP_011004894.1
Pe_27 WP_011004894.1
pe3_WP_016722261

pe61 KPJNPNMP_00768
pe9_BANHGPCM_00727
pe9 BANHGPCM_00727
to1_JICADCBL_00722
to1 JICADCBL_00722
to28_IIHHNEFC_02984
to28 IIHHNEFC_02984
to36_FAFFGKOF_00714
to36 FAFFGKOF_00714
to53_GDEOEPAP_00680
to53 GDEOEPAP_00680
to63_BFOHDJIN_00687
to63 BFOHDJIN_00687
to7_HOLBGOEP_00774
to7 HOLBGOEP_00774
pe1_WP_225891652.1
Pe_1 WP_225891652.1
pe13_AIELFPIA_01380
pe13 AIELFPIA_01380
pe15_BODOBMNI_01416
pe15 BODOBMNI_01416
pe18_NICADNEC_02919
pe18_round_3.fasta NICADNEC_02919
pe26_NCAEKIBJ_01355
pe26 NCAEKIBJ_01355
pe27_WP_209317695.1
Pe_27 WP_209317695.1
pe3_WP_209317242.1
Pe_3 WP_209317242.1
pe30_EENJCLCO_01376
pe30 EENJCLCO_01376
pe39_WP_209319322.1
Pe_39 WP_209319322.1
pe56_HFPKLCHG_01325
pe56 HFPKLCHG_01325
pe57_WP_209318858.1
Pe_57 WP_209318858.1
pe61_KPJNPNMP_01359
pe61 KPJNPNMP_01359
pe9_BANHGPCM_01357
pe9 BANHGPCM_01357
to1_JICADCBL_01395
to1 JICADCBL_01395
to28_IIHHNEFC_02373
to28 IIHHNEFC_02373
to36_FAFFGKOF_01344
to36 FAFFGKOF_01344
to53_GDEOEPAP_01269
to53 GDEOEPAP_01269
to63_BFOHDJIN_0

pe15_BODOBMNI_04691
pe15 BODOBMNI_04691
pe18_NICADNEC_04596
pe18_round_3.fasta NICADNEC_04596
pe26_NCAEKIBJ_04062
pe26 NCAEKIBJ_04062
pe27_WP_021156189.1
Pe_27 WP_021156189.1
pe3_WP_118888203.1
Pe_3 WP_118888203.1
pe30_EENJCLCO_04598
pe30 EENJCLCO_04598
pe39_WP_165858702.1
Pe_39 WP_165858702.1
pe56_HFPKLCHG_04509
pe56 HFPKLCHG_04509
pe57_WP_167798397.1
Pe_57 WP_167798397.1
pe61_KPJNPNMP_04600
pe61 KPJNPNMP_04600
pe9_BANHGPCM_04564
pe9 BANHGPCM_04564
to1_JICADCBL_04950
to1 JICADCBL_04950
to28_IIHHNEFC_04543
to28 IIHHNEFC_04543
to36_FAFFGKOF_04675
to36 FAFFGKOF_04675
to53_GDEOEPAP_03962
to53 GDEOEPAP_03962
to63_BFOHDJIN_04162
to63 BFOHDJIN_04162
to7_HOLBGOEP_04530
to7 HOLBGOEP_04530
pe1_WP_225891709.1
Pe_1 WP_225891709.1
pe13_AIELFPIA_04671
pe13 AIELFPIA_04671
pe15_BODOBMNI_04643
pe15 BODOBMNI_04643
pe18_NICADNEC_04548
pe18_round_3.fasta NICADNEC_04548
pe26_NCAEKIBJ_04109
pe26 NCAEKIBJ_04109
pe27_WP_011004276.1
Pe_27 WP_011004276.1
pe3_WP_011004276.1
Pe_3 WP_011004276.1
pe30_EENJCLCO_046

pe26_NCAEKIBJ_04891
pe26 NCAEKIBJ_04891
pe27_WP_071507083.1
Pe_27 WP_071507083.1
pe3_WP_064047918.1
Pe_3 WP_064047918.1
pe30_EENJCLCO_03818
pe30 EENJCLCO_03818
pe39_WP_071507083.1
Pe_39 WP_071507083.1
pe56_HFPKLCHG_03753
pe56 HFPKLCHG_03753
pe57_WP_071507083.1
Pe_57 WP_071507083.1
pe61_KPJNPNMP_03846
pe61 KPJNPNMP_03846
pe9_BANHGPCM_03744
pe9 BANHGPCM_03744
to1_JICADCBL_03889
to1 JICADCBL_03889
to28_IIHHNEFC_03802
to28 IIHHNEFC_03802
to36_FAFFGKOF_03854
to36 FAFFGKOF_03854
to53_GDEOEPAP_03395
to53 GDEOEPAP_03395
to63_BFOHDJIN_03728
to63 BFOHDJIN_03728
to7_HOLBGOEP_03775
to7 HOLBGOEP_03775
pe1_WP_225891752.1
Pe_1 WP_225891752.1
pe13_AIELFPIA_03879
pe13 AIELFPIA_03879
pe15_BODOBMNI_03845
pe15 BODOBMNI_03845
pe18_NICADNEC_03750
pe18_round_3.fasta NICADNEC_03750
pe26_NCAEKIBJ_04921
pe26 NCAEKIBJ_04921
pe27_WP_038937612.1
Pe_27 WP_038937612.1
pe3_WP_038937612.1
Pe_3 WP_038937612.1
pe30_EENJCLCO_03790
pe30 EENJCLCO_03790
pe39_WP_089190982.1
Pe_39 WP_089190982.1
pe56_HFPKLCHG_03721
pe56 HFPKL

# Test the position mapping
+ grab sequences from the original gb files using g2pos, g2strand and g2chr
+ load exported core OG nucleotide fasta file
+ compare the sequences 

(note: reverse compliment!)

In [78]:
if DEBUG:
    # for the compliment strand mapping
    from Bio.Seq import Seq
    Seq("A").complement()

In [79]:
if DEBUG:
    import os
    gbks = '/Users/devseeva/Desktop/work/pan-genome-visualization/data/rso_test/input_GenBank'
    ccc=0

    test_fasta = {}
    for entry in os.scandir(gbks):
        #if ccc>0:
        #    break
        ccc = ccc+1
        if (entry.path.endswith(".gbk") and entry.is_file()):
            genome = os.path.basename(entry).replace('_genomic.gbk', '_protein')
            test_fasta[genome] = []
            print('Genome:', genome)

            # map chr id to the sequence
            chr_seq = {}
            for record in SeqIO.parse(entry.path, "gb"):
                print('Chr',record.id, 'with', len(record.features), 'features')
                chr_seq[record.id] = record.seq

            # get corresponding mapping (from above)
            mapping_chr = g2chr[genome]
            mapping_pos = g2pos[genome]
            mapping_str = g2strand[genome]
            assert(len(mapping_chr) == len(mapping_pos))

            # iterate through the original positions 
            for i in range(len(mapping_chr)):
                if mapping_str[i] == 1:
                    test_fasta[genome].append(chr_seq[mapping_chr[i]][mapping_pos[i]])
                else:
                    compl = str(Seq(chr_seq[mapping_chr[i]][mapping_pos[i]]).complement())
                    test_fasta[genome].append(compl)
            test_fasta[genome] = "".join(test_fasta[genome])
            print("Core nucl exported:", len(test_fasta[genome]))

            print()
            

In [80]:
if DEBUG:

    for record in SeqIO.parse("core_OG_nucl.fasta", "fasta"):
        print(record.id, len(record.seq))
        print('test length', len(record.seq))
        print('Test:', test_fasta[record.id] == str(record.seq))
        print()


f = "/Users/devseeva/Desktop/work/pan-genome-visualization/data/ncbi-rso/metainfo.tsv"
x = pd.read_csv(f, sep='\t')  
phys = []
for a in x["accession"]:
    phys.append(a.split(".1_")[1][:10])
x["phy_id"] = phys
x.to_csv("/Users/devseeva/Desktop/work/sm_workflow/snakefiles/inputs/phy4_test_metadata/phy4_test_cleaned_data.csv", index=False)